# Connecting to the board

In [1]:
import samna
print(f'Samna version {samna.__version__}')

import numpy as np
import matplotlib.pyplot as plt
from rockpool.devices.xylo.syns65302 import config_from_specification as config_from, mapper as mapper, XyloSamna as XyloSamna, XyloMonitor as XyloMonitor
from rockpool.devices.xylo.syns65302 import xa3_devkit_utils as hdu

from rockpool.transform.quantize_methods import channel_quantize

Samna version 0.39.9.0


In [2]:
# - Getting the connected devices and choosing xyloa3 board
xylo_node = hdu.find_xylo_a3_boards()[0]

print(xylo_node)


## Clock frequencies

In [3]:
clock_frequencies = [6.25, 12.5, 25, 50]

## Configuration to read registers

In [4]:
import samna
print(f"samna version: {samna.__version__}")
import time

# set device configuration
ioc = xylo_node.get_io_control_module()
io = xylo_node.get_io_module()
model = xylo_node.get_model()


def read_register(addr):
    source.write([samna.xyloAudio3.event.ReadRegisterValue(address = addr)])
    events = sink.get_n_events(1, 3000)
    assert(len(events) == 1)
    return events[0].data

ctrl1 = 0x0001
ctrl2 = 0x0002
ctrl3 = 0x0003
tr_wrap = 0x0004
hm_tr_wrap = 0x0005
clk_ctrl = 0x0006
clk_div = 0x0007
pwr_ctrl1 = 0x0008
pwr_ctrl2 = 0x0009
pwr_ctrl3 = 0x000A
pwr_ctrl4 = 0x000B
pad_ctrl = 0x000C
ie1 = 0x000E
ie2 = 0x000F
out_ctrl = 0x0011
monsel = 0x0166
mon_grp_sel = 0x0167
dbg_ctrl1 = 0x0168
dbg_stat1 = 0x0171
dfe_ctrl = 0x001B
ivgen = 0x0015
ivgen2 = 0x0016
ivgen3 = 0x0017
ivgen4 = 0x0018
ivgen5 = 0x0019
ivgen6 = 0x001A
adctest = 0x016E

# create access to xylo input/output
source = samna.graph.source_to(model.get_sink_node())
sink   = samna.graph.sink_from(model.get_source_node())


# print("\n# ======= read important registers =======\n")

# print(f"adctest       : 0x{format(read_register(adctest),'_X')}")
# print(f"ivgen       : 0x{format(read_register(ivgen),'_X')}")
# print(f"ivgen2       : 0x{format(read_register(ivgen2),'_X')}")
# print(f"ivgen3       : 0x{format(read_register(ivgen3),'_X')}")
# print(f"ivgen4       : 0x{format(read_register(ivgen4),'_X')}")
# print(f"ivgen5       : 0x{format(read_register(ivgen5),'_X')}")
# print(f"ivgen6       : 0x{format(read_register(ivgen6),'_X')}")
# # # ctrl[1-3]
# print(f"ctrl1       : 0x{format(read_register(ctrl1),'_X')}")
# print(f"ctrl2       : 0x{format(read_register(ctrl2),'_X')}")
# print(f"ctrl3       : 0x{format(read_register(ctrl3),'_X')}")
# print()
# # *_wrap
# print(f"tr_wrap     : 0x{format(read_register(tr_wrap),'_X')}")
# print(f"hm_tr_wrap  : 0x{format(read_register(hm_tr_wrap),'_X')}")
# print()
# # clk_*
# print(f"clk_ctrl    : 0x{format(read_register(clk_ctrl),'_X')}")
# print(f"clk_div     : 0x{format(read_register(clk_div),'_X')}")
# print()
# # pwr_ctrl[1-4]
# print(f"pwr_ctrl1   : 0x{format(read_register(pwr_ctrl1),'_X')}")
# print(f"pwr_ctrl2   : 0x{format(read_register(pwr_ctrl2),'_X')}")
# print(f"pwr_ctrl3   : 0x{format(read_register(pwr_ctrl3),'_X')}")
# print(f"pwr_ctrl4   : 0x{format(read_register(pwr_ctrl4),'_X')}")
# print()
# # misc
# print(f"pad_ctrl    : 0x{format(read_register(pad_ctrl),'_X')}")
# print(f"ie1         : 0x{format(read_register(ie1),'_X')}")
# print(f"ie2         : 0x{format(read_register(ie2),'_X')}")
# print(f"out_ctrl    : 0x{format(read_register(out_ctrl),'_X')}")
# print()
# # debug regs
# print(f"monsel      : 0x{format(read_register(monsel),'_X')}")
# print(f"mon_grp_sel : 0x{format(read_register(mon_grp_sel),'_X')}")
# print(f"dbg_ctrl1   : 0x{format(read_register(dbg_ctrl1),'_X')}")
# print(f"dbg_stat1   : 0x{format(read_register(dbg_stat1),'_X')}")
# print(f"dfe_ctrl   : 0x{format(read_register(dfe_ctrl),'_X')}")


samna version: 0.39.9.0


# Power measurement - iddle - no network

In [5]:
dt = 0.01 # seconds
duration = 3 # seconds

power_consumption_io = []
power_consumption_analog = []
power_consumption_digital = []

# - For every clock rate we want to measure
for clock in clock_frequencies:

    io_power = []
    analog_power = []
    digital_power = []

    # Instantiate XyloMonitor and call evolve for three second in silence
    xylo_monitor = XyloMonitor(device=xylo_node, main_clk_rate=clock, config=None, power_frequency=100, dt=dt, output_mode='Spike')

    # sink.clear_events()
    # print(clock)
    # print(f"tr_wrap     : 0x{format(read_register(tr_wrap),'_X')}")
    # # pwr_ctrl[1-4]
    # print(f"pwr_ctrl1   : 0x{format(read_register(pwr_ctrl1),'_X')}")
    # print(f"pwr_ctrl2   : 0x{format(read_register(pwr_ctrl2),'_X')}")
    # print(f"pwr_ctrl3   : 0x{format(read_register(pwr_ctrl3),'_X')}")
    # print(f"pwr_ctrl4   : 0x{format(read_register(pwr_ctrl4),'_X')}")

    # - Run ten times to average all samples
    for i in range(20):

        out, state, rec = xylo_monitor.evolve(read_timeout=duration, record_power=True)

        io_power.append(np.mean(rec['io_power']))
        analog_power.append (np.mean(rec['analog_power']))
        digital_power.append(np.mean(rec['digital_power']))

    xylo_monitor = []
    power_consumption_io+=[np.mean(io_power)]
    power_consumption_analog+=[np.mean(analog_power)]
    power_consumption_digital+=[np.mean(digital_power)]

for clock, io, analog, digital in zip(clock_frequencies, power_consumption_io, power_consumption_analog, power_consumption_digital):
    print(f'Clock:\t{clock} MHz\nio:\t{io*1000:.1f} mW \t AFE core:\t{analog*1000:.1f} mW\tSNN core logic:\t{digital*1000:.1f} mW')

events received:
[xyloAudio3::event::Readout(timestep=0, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=1, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=2, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=3, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=4, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=5, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio3::event::Readout(timestep=6, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 1 }), xyloAudio

## Load a network to the chip

In [6]:
from rockpool.nn.networks import SynNet
from rockpool.nn.modules import LIFTorch
import warnings
warnings.filterwarnings("ignore")

ckpt = '../../../docs/devices/xylo-a3/model_sample/to_deploy_inXylo.json'

# - Loading trained model architecture parameters
arch_params = {'n_classes': 1,
'n_channels': 16,
'size_hidden_layers':[63, 63, 63],
'time_constants_per_layer':[3,7,7],
'tau_syn_base': 0.02,
'tau_mem': 0.02,
'tau_syn_out': 0.02,
'neuron_model': LIFTorch,
'dt': 0.00994,
'output': 'vmem'}

# - Instantiating the model backbone and loading trained checkpoint
model = SynNet(** arch_params)
model.load(ckpt)

from rockpool.devices.xylo.syns65302 import config_from_specification, mapper
import rockpool.transform.quantize_methods as q

# getting the model specifications using the mapper function
spec = mapper(model.as_graph(), weight_dtype='float', threshold_dtype='float', dash_dtype='float')
# quantizing the model
spec.update(q.channel_quantize(**spec))

xylo_conf, is_valid, msg = config_from_specification(**spec)

print(xylo_conf)


WARNING    /home/vleite/SynSense/rockpool/rockpool/nn/networks/__init__.py:15: UserWarning: This module needs to be ported to the v2 API.
  warnings.warn(f"{err}")
 [py.warnings]
  warnings.warn(f"{err}")

WARNING    /home/vleite/SynSense/rockpool/rockpool/nn/networks/__init__.py:20: UserWarning: This module needs to be ported to the v2 API.
  warnings.warn(f"{err}")
 [py.warnings]
  warnings.warn(f"{err}")



xyloAudio3::configuration::XyloConfiguration(operation_mode=OperationMode.AcceleratedTime, input_source=InputSource.SpikeEvents, synapse2_enable=0, bias_enable=1, time_resolution_wrap=0, output_counter_wrap=0, enable_hibernation_mode=0, hibernation_mode_time_resolution_wrap=0, input=xyloAudio3::configuration::InputConfig(weight_bit_shift=0, weights={ -61 -35 91 39 -68 -43 127 22 33 6 -12 -3 39 -41 76 22 22 29 -20 -127 38 -20 22 0 -59 16 -43 -44 -16 21 -14 -59 24 90 5 -26 65 -44 49 -43 54 46 68 -61 -105 48 -5 2 -22 -17 12 127 6 44 -38 33 -127 -1 108 -100 127 15 127 5 127 49 20 -32 -127 79 26 31 -81 -17 0 111 127 -127 -34 -111 -45 -52 -46 -17 -74 -7 -45 73 -85 -26 -32 -63 -27 -46 -32 -127 38 -15 -10 9 -10 -18 93 -2 -43 40 -14 104 116 26 18 34 -127 -127 87 23 21 100 66 -84 -50 -65 24 24 -75 -52 -74 -64 109 15 38 -66 90 1 8 -51 -49 123 -90 -8 -64 -79 122 -47 127 62 12 82 -17 30 -9 -127 2 -15 -125 16 -69 -63 15 47 41 -31 6 -14 -127 -87 -42 -42 -47 73 60 127 59 -63 -32 -27 -37 22 0 3 -22 -93

# Power measurement - iddle - with loaded network

In [7]:
clock_frequencies = [12.5, 25, 50]

In [8]:
xylo_conf.operation_mode = samna.xyloAudio3.OperationMode.RealTime

dt = 0.01 # seconds
duration = 3 # seconds

power_consumption_io = []
power_consumption_analog = []
power_consumption_digital = []

# - For every clock rate we want to measure
for clock in clock_frequencies:

    io_power = []
    analog_power = []
    digital_power = []

    # Instantiate XyloMonitor and call evolve for three second in silence
    xylo_monitor = XyloMonitor(device=xylo_node, main_clk_rate=clock, config=xylo_conf, power_frequency=100, dt=dt, output_mode='Spike')

    # sink.clear_events()
    # print(clock)
    # print(f"tr_wrap     : 0x{format(read_register(tr_wrap),'_X')}")
    # # pwr_ctrl[1-4]
    # print(f"pwr_ctrl1   : 0x{format(read_register(pwr_ctrl1),'_X')}")
    # print(f"pwr_ctrl2   : 0x{format(read_register(pwr_ctrl2),'_X')}")
    # print(f"pwr_ctrl3   : 0x{format(read_register(pwr_ctrl3),'_X')}")
    # print(f"pwr_ctrl4   : 0x{format(read_register(pwr_ctrl4),'_X')}")

    # - Run ten times to average all samples
    for i in range(20):
        out, state, rec = xylo_monitor.evolve(read_timeout=duration, record_power=True)

        io_power.append(np.mean(rec['io_power']))
        analog_power.append (np.mean(rec['analog_power']))
        digital_power.append(np.mean(rec['digital_power']))

    xylo_monitor = []

    power_consumption_io+=[np.mean(io_power)]
    power_consumption_analog+=[np.mean(analog_power)]
    power_consumption_digital+=[np.mean(digital_power)]


for clock, io, analog, digital in zip(clock_frequencies, power_consumption_io, power_consumption_analog, power_consumption_digital):
    # print(power)
    print(f'Clock:\t{clock} MHz\nio:\t{io*1000:.1f} mW \t AFE core:\t{analog*1000:.1f} mW\tSNN core logic:\t{digital*1000:.1f} mW')

events received:
[xyloAudio3::event::Readout(timestep=0, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=1, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=2, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=3, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 2 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=4, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 5 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=5, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ -3 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=6, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ -7 }, output_spikes={ 0 }), xyloAud

# Power measurement - inference over a trained network

In [9]:
from scipy.io import wavfile
!pip install simpleaudio
import simpleaudio as sa
import numpy as np

def get_wave_object(test_file):
    sample_rate, data = wavfile.read(test_file)

    duration = int(len(data)/sample_rate) # in seconds
    n = data.ndim

    if data.dtype == np.int8:
        bytes_per_sample = 1
    elif data.dtype == np.int16:
        bytes_per_sample = 2
    elif data.dtype == np.float32:
        bytes_per_sample = 4
    else:
        raise ValueError("recorded audio should have 1 or 2 bytes per sample!")

    wave_obj = sa.WaveObject(
        audio_data= data,
        num_channels=data.ndim,
        bytes_per_sample=bytes_per_sample,
        sample_rate=sample_rate
    )

    return duration,wave_obj

Defaulting to user installation because normal site-packages is not writeable


In [10]:
xylo_conf.operation_mode = samna.xyloAudio3.OperationMode.RealTime

dt = 0.01 # seconds
duration = 3 # seconds

power_consumption_io = []
power_consumption_analog = []
power_consumption_digital = []

# - For every clock rate we want to measure
for clock in clock_frequencies:

    io_power = []
    analog_power = []
    digital_power = []

    # Instantiate XyloMonitor and call evolve for three seconds playing an audio
    xylo_monitor = XyloMonitor(device=xylo_node, main_clk_rate=clock, config=xylo_conf, power_frequency=100, dt=dt, output_mode='Spike')

    # sink.clear_events()
    # print(clock)
    # print(f"tr_wrap     : 0x{format(read_register(tr_wrap),'_X')}")
    # # pwr_ctrl[1-4]
    # print(f"pwr_ctrl1   : 0x{format(read_register(pwr_ctrl1),'_X')}")
    # print(f"pwr_ctrl2   : 0x{format(read_register(pwr_ctrl2),'_X')}")
    # print(f"pwr_ctrl3   : 0x{format(read_register(pwr_ctrl3),'_X')}")
    # print(f"pwr_ctrl4   : 0x{format(read_register(pwr_ctrl4),'_X')}")

    # - Run ten times to average all samples
    for i in range(20):
        test_audio = '../../../docs/devices/xylo-a3/audio_sample/cry_sample_3sec.wav'
        duration, wave_obj = get_wave_object(test_audio)
        
        play_obj = wave_obj.play()
        out, state, rec = xylo_monitor.evolve(read_timeout=duration, record_power=True)
        play_obj.wait_done()
        
        print(f'cry detected: {np.sum(out)>0}')

        io_power.append(np.mean(rec['io_power']))
        analog_power.append (np.mean(rec['analog_power']))
        digital_power.append(np.mean(rec['digital_power']))

    xylo_monitor = []

    power_consumption_io+=[np.mean(io_power)]
    power_consumption_analog+=[np.mean(analog_power)]
    power_consumption_digital+=[np.mean(digital_power)]


for clock, io, analog, digital in zip(clock_frequencies, power_consumption_io, power_consumption_analog, power_consumption_digital):
    # print(power)
    print(f'Clock:\t{clock} MHz\nio:\t{io*1000:.1f} mW \t AFE core:\t{analog*1000:.1f} mW\tSNN core logic:\t{digital*1000:.1f} mW')

events received:
[xyloAudio3::event::Readout(timestep=0, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=1, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=2, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=3, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 2 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=4, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 1 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=5, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ -4 }, output_spikes={ 0 }), xyloAudio3::event::Readout(timestep=6, neuron_v_mems={ }, neuron_i_syns={ }, hidden_spikes={ }, output_v_mems={ 0 }, output_spikes={ 0 }), xyloAudi

## Power measurement with Samna only

In [11]:
import samna
print(f'Samna version {samna.__version__}')

# Open the device and connect it to the power monitor.
# xylo_node = samna.device.open_device("XyloAudio3TestBoard")

# when running all the cells in this notebook, the board is already open

power_monitor = xylo_node.get_power_monitor()
sink_pm = samna.graph.sink_from(power_monitor.get_source_node())
stopwatch = xylo_node.get_stop_watch()
io = xylo_node.get_io_module()

# clock_frequencies = [0, 0.012207031, 0.024414063, 0.048828125, 0.09765625, 0.1953125, 0.390625, 0.78125, 1.5625, 3.125, 6.25, 12.5, 25, 50]

# write_config = [0, 4095, 2047, 1023, 511, 255, 127, 63, 31, 15, 7, 3, 1, 0]

clock_frequencies = [6.25, 12.5, 25, 50]
write_config = [7, 3, 1, 0]

ts = 1e-3

power_consumption = []
for clock, value in zip(clock_frequencies, write_config):
    # print(clock)

    config = samna.xyloAudio3.XyloAudio3TestBoardDefaultConfig()
    config.main_clock_frequency = int(clock * 1000000)
    xylo_node.reset_board_soft(config)


    main_clk_freq = clock * 1e6  # in Hz
    tr_wrap = int(ts * main_clk_freq)
    
    config = samna.xyloAudio3.configuration.XyloConfiguration()
    # config.operation_mode = samna.xyloAudio3.OperationMode.RealTime
    # config.digital_frontend.filter_bank.dn_enable = False
    # config.time_resolution_wrap = tr_wrap
    # config.debug.always_update_omp_stat = True
    # config.digital_frontend.filter_bank.use_global_iaf_threshold = False
    # config.input_source = samna.xyloAudio3.InputSource.DigitalMicrophone
    # # - the ideal sdm clock ratio depends on the main clock rate
    # config.debug.sdm_clock_ratio = int(clock / 1.56 / 2 - 1)
    # config.digital_frontend.pdm_preprocessing.clock_direction = 1
    # config.digital_frontend.pdm_preprocessing.clock_edge = 0
    
    # # - Disable internal state monitoring
    # config.debug.monitor_neuron_v_mem = []
    # config.debug.monitor_neuron_spike = []
    # config.debug.monitor_neuron_i_syn = []

    # xylo_node.get_model().apply_configuration(config)



    # if clock == 0:
    #     io.write_config(0x0008, value)
    # else:
    #     io.write_config(0x0007, value)    

    # Start the stopwatch to enable time-stamped power sampling.
    stopwatch.start()
    
    # Start sampling power on all channels at a rate of 100 Hz.
    power_monitor.start_auto_power_measurement(100)
    
    # Auto power measurement streams PowerMeasurement events continuously.
    # To capture 3 seconds of data from 3 channels at 100Hz, we collect 900 events.
    events = sink_pm.get_n_events(900, timeout=4000)
    
    # Stop the automatic power measurement process.
    power_monitor.stop_auto_power_measurement()
    
    # Calculate the average power consumption for each channel over 3 seconds.
    counts = [0, 0, 0]
    sums = [0, 0, 0]
    for e in events:
        assert isinstance(e, samna.unifirm.modules.events.PowerMeasurement)
        sums[e.channel] += e.value
        counts[e.channel] += 1
    
    # Compute the averages and convert to milliwatts (W -> mW).
    avgs = [sum/count * 1000 for sum, count in zip(sums, counts)]
    # print(avgs)
    power_consumption+= [avgs]

for clock, power in zip(clock_frequencies, power_consumption):
    # print(power)
    print(f'Clock:\t{clock} MHz\nio:\t{io*1000:.1f} mW \t AFE core:\t{analog*1000:.1f} mW\tSNN core logic:\t{digital*1000:.1f} mW')

Samna version 0.39.9.0


TypeError: unsupported operand type(s) for *: 'samna.xyloAudio3.UnifirmModule' and 'int'

In [ ]:
1.38 / 2.5 = 0.552 mA = 552 uA